In [1]:
import torch
from utils.dataset import JSONTrackDataset
from torch.utils.data import DataLoader

In [2]:
from model_linear import TrackModel
from functools import reduce

In [3]:
list = [1, 2, 3, 4]
reduce(lambda a,b: a + b, list)

10

In [4]:
model = TrackModel()
sum([p.numel() for p in model.parameters()])

9538

In [5]:
model = torch.load('model.pt', map_location=torch.device('cpu'))
model.eval()

TrackModel(
  (net): Sequential(
    (0): Linear(in_features=16, out_features=64, bias=True)
    (1): ReLU(inplace=True)
    (2): Linear(in_features=64, out_features=64, bias=True)
    (3): ReLU(inplace=True)
    (4): Linear(in_features=64, out_features=64, bias=True)
    (5): ReLU(inplace=True)
    (6): Dropout(p=0.4, inplace=False)
    (7): Linear(in_features=64, out_features=2, bias=True)
  )
)

In [6]:
dataset = JSONTrackDataset('data_4/val.json')
dataset[0]
dataset[0]['data'].size()

torch.Size([1, 4, 4])

In [7]:
dataset = JSONTrackDataset('data_4/train.json')
dummy = dataset[100]['data']
dummy.size()
dummy = torch.randn(1, 1, 4, 4)
torch.onnx.export(model, dummy, "coord_net_linear.onnx", verbose=True)
model(torch.randn(1, 1, 4, 4))

graph(%0 : Float(1, 1, 4, 4),
      %net.0.weight : Float(64, 16),
      %net.0.bias : Float(64),
      %net.2.weight : Float(64, 64),
      %net.2.bias : Float(64),
      %net.4.weight : Float(64, 64),
      %net.4.bias : Float(64),
      %net.7.weight : Float(2, 64),
      %net.7.bias : Float(2)):
  %9 : Long() = onnx::Constant[value={0}](), scope: TrackModel
  %10 : Tensor = onnx::Shape(%0), scope: TrackModel
  %11 : Long() = onnx::Gather[axis=0](%10, %9), scope: TrackModel # /home/nikolay/dev/DroneNet/coords_pub/model_linear.py:22:0
  %12 : Long() = onnx::Constant[value={-1}](), scope: TrackModel
  %13 : Tensor = onnx::Unsqueeze[axes=[0]](%11)
  %14 : Tensor = onnx::Unsqueeze[axes=[0]](%12)
  %15 : Tensor = onnx::Concat[axis=0](%13, %14)
  %16 : Float(1, 16) = onnx::Reshape(%0, %15), scope: TrackModel # /home/nikolay/dev/DroneNet/coords_pub/model_linear.py:22:0
  %17 : Float(1, 64) = onnx::Gemm[alpha=1, beta=1, transB=1](%16, %net.0.weight, %net.0.bias), scope: TrackModel/Sequentia

tensor([[ 32.5051, -32.6809]], grad_fn=<AddmmBackward>)

In [8]:
dataset = JSONTrackDataset('data_4/val.json')
len(dataset)

48328

In [9]:
item = 718
print(dataset[item])
d = torch.stack([dataset[item]['data']])
model(d)

{'label': tensor([0, 1]), 'data': tensor([[[669., 278.,  13.,  13.],
         [668., 278.,  13.,  13.],
         [665., 277.,  12.,  13.],
         [662., 277.,  13.,  13.]]])}


tensor([[-1.9371,  1.8095]], grad_fn=<AddmmBackward>)

In [10]:
drone = torch.tensor([[
          [1577.,  679.,    3.,    3.],
          [1577.,  679.,    3.,    3.],
          [1577.,  679.,    3.,    3.],
          [1577.,  679.,    3.,    3.]]])
s = torch.stack([drone])
model(s)

tensor([[ 14.1524, -14.0287]], grad_fn=<AddmmBackward>)

In [11]:
for idx, i in enumerate(dataset):
    print(idx, i['label'], model(torch.stack([i['data']])))

0 tensor([1, 0]) tensor([[ 10.8311, -10.8514]], grad_fn=<AddmmBackward>)
1 tensor([1, 0]) tensor([[ 27.7587, -27.6848]], grad_fn=<AddmmBackward>)
2 tensor([1, 0]) tensor([[ 60.4864, -60.4253]], grad_fn=<AddmmBackward>)
3 tensor([1, 0]) tensor([[ 10.6529, -10.6304]], grad_fn=<AddmmBackward>)
4 tensor([1, 0]) tensor([[ 10.6529, -10.6304]], grad_fn=<AddmmBackward>)
5 tensor([1, 0]) tensor([[ 10.6529, -10.6304]], grad_fn=<AddmmBackward>)
6 tensor([1, 0]) tensor([[ 9.4382, -9.4298]], grad_fn=<AddmmBackward>)
7 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmBackward>)
8 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmBackward>)
9 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmBackward>)
10 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmBackward>)
11 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmBackward>)
12 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmBackward>)
13 tensor([1, 0]) tensor([[ 9.3550, -9.3340]], grad_fn=<AddmmB

251 tensor([1, 0]) tensor([[ 4.6506, -4.6076]], grad_fn=<AddmmBackward>)
252 tensor([1, 0]) tensor([[-0.2927,  0.3760]], grad_fn=<AddmmBackward>)
253 tensor([1, 0]) tensor([[-1.6602,  1.4951]], grad_fn=<AddmmBackward>)
254 tensor([1, 0]) tensor([[ 2.3213, -2.3638]], grad_fn=<AddmmBackward>)
255 tensor([1, 0]) tensor([[-2.4405,  2.2205]], grad_fn=<AddmmBackward>)
256 tensor([1, 0]) tensor([[ 11.7909, -11.6126]], grad_fn=<AddmmBackward>)
257 tensor([1, 0]) tensor([[ 2029.3372, -2034.1107]], grad_fn=<AddmmBackward>)
258 tensor([1, 0]) tensor([[ 2309.7200, -2316.4717]], grad_fn=<AddmmBackward>)
259 tensor([1, 0]) tensor([[ 2124.4250, -2128.7988]], grad_fn=<AddmmBackward>)
260 tensor([1, 0]) tensor([[ 67.5634, -67.4632]], grad_fn=<AddmmBackward>)
261 tensor([1, 0]) tensor([[-0.7328,  0.6907]], grad_fn=<AddmmBackward>)
262 tensor([1, 0]) tensor([[-0.7238,  0.7090]], grad_fn=<AddmmBackward>)
263 tensor([1, 0]) tensor([[ 6.2173, -6.1109]], grad_fn=<AddmmBackward>)
264 tensor([1, 0]) tensor([[ 

465 tensor([1, 0]) tensor([[-0.2203,  0.0021]], grad_fn=<AddmmBackward>)
466 tensor([1, 0]) tensor([[ 3.4306, -3.4316]], grad_fn=<AddmmBackward>)
467 tensor([1, 0]) tensor([[ 3.4306, -3.4316]], grad_fn=<AddmmBackward>)
468 tensor([1, 0]) tensor([[ 3.4306, -3.4316]], grad_fn=<AddmmBackward>)
469 tensor([1, 0]) tensor([[ 4.5497, -4.5693]], grad_fn=<AddmmBackward>)
470 tensor([1, 0]) tensor([[ 0.4314, -0.3884]], grad_fn=<AddmmBackward>)
471 tensor([1, 0]) tensor([[ 0.4314, -0.3884]], grad_fn=<AddmmBackward>)
472 tensor([1, 0]) tensor([[ 5.6218, -5.7265]], grad_fn=<AddmmBackward>)
473 tensor([1, 0]) tensor([[ 5.6218, -5.7265]], grad_fn=<AddmmBackward>)
474 tensor([1, 0]) tensor([[ 5.6218, -5.7265]], grad_fn=<AddmmBackward>)
475 tensor([1, 0]) tensor([[ 4.1420, -4.1088]], grad_fn=<AddmmBackward>)
476 tensor([1, 0]) tensor([[ 20.4845, -20.4979]], grad_fn=<AddmmBackward>)
477 tensor([1, 0]) tensor([[ 0.4854, -0.4951]], grad_fn=<AddmmBackward>)
478 tensor([1, 0]) tensor([[ 16.4703, -15.9345]],

651 tensor([1, 0]) tensor([[ 6.0874, -6.1066]], grad_fn=<AddmmBackward>)
652 tensor([1, 0]) tensor([[ 23.8224, -24.1688]], grad_fn=<AddmmBackward>)
653 tensor([1, 0]) tensor([[ 20.9682, -20.8573]], grad_fn=<AddmmBackward>)
654 tensor([1, 0]) tensor([[ 2.8357, -2.7523]], grad_fn=<AddmmBackward>)
655 tensor([1, 0]) tensor([[ 4.2755, -4.2229]], grad_fn=<AddmmBackward>)
656 tensor([1, 0]) tensor([[ 12.8745, -13.0638]], grad_fn=<AddmmBackward>)
657 tensor([1, 0]) tensor([[ 0.7315, -0.6885]], grad_fn=<AddmmBackward>)
658 tensor([1, 0]) tensor([[ 6.1595, -6.0982]], grad_fn=<AddmmBackward>)
659 tensor([1, 0]) tensor([[ 7.7171, -7.4945]], grad_fn=<AddmmBackward>)
660 tensor([1, 0]) tensor([[ 1.7851, -1.7771]], grad_fn=<AddmmBackward>)
661 tensor([1, 0]) tensor([[ 1.7851, -1.7771]], grad_fn=<AddmmBackward>)
662 tensor([1, 0]) tensor([[ 1.7851, -1.7771]], grad_fn=<AddmmBackward>)
663 tensor([1, 0]) tensor([[ 5.0141, -5.0378]], grad_fn=<AddmmBackward>)
664 tensor([1, 0]) tensor([[ 6.6049, -6.6185]

903 tensor([1, 0]) tensor([[ 7.6427, -7.3968]], grad_fn=<AddmmBackward>)
904 tensor([1, 0]) tensor([[ 11.2889, -11.2087]], grad_fn=<AddmmBackward>)
905 tensor([1, 0]) tensor([[ 13.2498, -13.1132]], grad_fn=<AddmmBackward>)
906 tensor([1, 0]) tensor([[ 0.8671, -0.9117]], grad_fn=<AddmmBackward>)
907 tensor([1, 0]) tensor([[ 1.1976, -1.4008]], grad_fn=<AddmmBackward>)
908 tensor([1, 0]) tensor([[ 0.2575, -0.4341]], grad_fn=<AddmmBackward>)
909 tensor([1, 0]) tensor([[-0.1407,  0.0338]], grad_fn=<AddmmBackward>)
910 tensor([1, 0]) tensor([[-0.3939,  0.2894]], grad_fn=<AddmmBackward>)
911 tensor([1, 0]) tensor([[ 5.7694, -5.7989]], grad_fn=<AddmmBackward>)
912 tensor([1, 0]) tensor([[ 6.5620, -6.6913]], grad_fn=<AddmmBackward>)
913 tensor([1, 0]) tensor([[ 2.2638, -2.1660]], grad_fn=<AddmmBackward>)
914 tensor([1, 0]) tensor([[ 0.4399, -0.3685]], grad_fn=<AddmmBackward>)
915 tensor([1, 0]) tensor([[ 5.7060, -5.6970]], grad_fn=<AddmmBackward>)
916 tensor([1, 0]) tensor([[ 17.2972, -17.1942]

...

47362 tensor([1, 0]) tensor([[ 61.9776, -61.8595]], grad_fn=<AddmmBackward>)
47363 tensor([1, 0]) tensor([[ 72.0391, -71.7632]], grad_fn=<AddmmBackward>)
47364 tensor([1, 0]) tensor([[ 76.8767, -76.5675]], grad_fn=<AddmmBackward>)
47365 tensor([1, 0]) tensor([[ 42.6770, -42.8930]], grad_fn=<AddmmBackward>)
47366 tensor([1, 0]) tensor([[ 46.4497, -46.6488]], grad_fn=<AddmmBackward>)
47367 tensor([1, 0]) tensor([[ 50.0859, -50.2845]], grad_fn=<AddmmBackward>)
47368 tensor([1, 0]) tensor([[ 51.9816, -52.1404]], grad_fn=<AddmmBackward>)
47369 tensor([1, 0]) tensor([[ 51.9816, -52.1404]], grad_fn=<AddmmBackward>)
47370 tensor([1, 0]) tensor([[ 3.8546, -3.8443]], grad_fn=<AddmmBackward>)
47371 tensor([1, 0]) tensor([[ 3.8546, -3.8443]], grad_fn=<AddmmBackward>)
47372 tensor([1, 0]) tensor([[ 14.4677, -14.2968]], grad_fn=<AddmmBackward>)
47373 tensor([1, 0]) tensor([[ 13.6909, -13.5117]], grad_fn=<AddmmBackward>)
47374 tensor([1, 0]) tensor([[ 21.5848, -21.3193]], grad_fn=<AddmmBackward>)
473

47563 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47564 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47565 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47566 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47567 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47568 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47569 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47570 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47571 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47572 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47573 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47574 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)
47575 tensor([1, 0]) tensor([[ 94.0157, -93.5750]], grad_fn=<AddmmBackward>)

47741 tensor([1, 0]) tensor([[ 76.2057, -76.1473]], grad_fn=<AddmmBackward>)
47742 tensor([1, 0]) tensor([[ 76.2057, -76.1473]], grad_fn=<AddmmBackward>)
47743 tensor([1, 0]) tensor([[ 76.2057, -76.1473]], grad_fn=<AddmmBackward>)
47744 tensor([1, 0]) tensor([[ 76.4765, -76.1720]], grad_fn=<AddmmBackward>)
47745 tensor([1, 0]) tensor([[ 11.6902, -11.6488]], grad_fn=<AddmmBackward>)
47746 tensor([1, 0]) tensor([[ 10.1615, -10.0154]], grad_fn=<AddmmBackward>)
47747 tensor([1, 0]) tensor([[ 23.1174, -23.3457]], grad_fn=<AddmmBackward>)
47748 tensor([1, 0]) tensor([[ 23.1174, -23.3457]], grad_fn=<AddmmBackward>)
47749 tensor([1, 0]) tensor([[ 23.1719, -23.3949]], grad_fn=<AddmmBackward>)
47750 tensor([1, 0]) tensor([[ 23.1719, -23.3949]], grad_fn=<AddmmBackward>)
47751 tensor([1, 0]) tensor([[ 8.8440, -8.7244]], grad_fn=<AddmmBackward>)
47752 tensor([1, 0]) tensor([[ 8.2322, -8.1252]], grad_fn=<AddmmBackward>)
47753 tensor([1, 0]) tensor([[ 7.3670, -7.2805]], grad_fn=<AddmmBackward>)
47754

47993 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
47994 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
47995 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
47996 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
47997 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
47998 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
47999 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
48000 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
48001 tensor([1, 0]) tensor([[ 92.2217, -91.7943]], grad_fn=<AddmmBackward>)
48002 tensor([1, 0]) tensor([[ 92.7626, -92.3353]], grad_fn=<AddmmBackward>)
48003 tensor([1, 0]) tensor([[ 92.9853, -92.5563]], grad_fn=<AddmmBackward>)
48004 tensor([1, 0]) tensor([[ 92.9853, -92.5563]], grad_fn=<AddmmBackward>)
48005 tensor([1, 0]) tensor([[ 92.9853, -92.5563]], grad_fn=<AddmmBackward>)

48232 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48233 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48234 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48235 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48236 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48237 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48238 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48239 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48240 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48241 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48242 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48243 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)
48244 tensor([1, 0]) tensor([[ 76.7758, -76.7596]], grad_fn=<AddmmBackward>)

In [48]:
print(dataset[467])
print(dataset[468])

{'label': tensor([1, 0]), 'data': tensor([[[655., 472.,  12.,  12.],
         [655., 472.,  12.,  12.],
         [655., 472.,  12.,  12.],
         [655., 472.,  12.,  12.]]])}
{'label': tensor([1, 0]), 'data': tensor([[[655., 472.,  12.,  12.],
         [655., 472.,  12.,  12.],
         [655., 472.,  12.,  12.],
         [655., 472.,  12.,  12.]]])}
